# JavaScripty with Mutable Variables

Note: this is more lecture notes than anything. As students expressed, I think this might help digest the reading a little. 
Please do not take this as official course materials. If you are struggling to understand the reading, you could look at these notes for some clues. 
There could be spelling or content errors, so don't take it as absolute truth, rely on the book for that. 

## AST 

In [10]:
trait Expr                                                     // e
case class N(n: Double) extends Expr                           // e ::= n
case class Var(x: String) extends Expr                         // e ::= x
case class VarDecl(x: String, e1: Expr, e2: Expr) extends Expr // e ::= var x = e1; e2
case class Assign(e1: Expr, e2: Expr) extends Expr             // e ::= e1 = e2
case class Deref(e1: Expr) extends Expr                        // e ::= *e1
case class A(a: Int) extends Expr                              // e ::= a

def isValue(e: Expr): Boolean = e match {
  case N(_) => true
  case _ => false
}

def isLValue(e: Expr): Boolean = e match {
  case Deref(A(_)) => true
  case _ => false
}

defined trait Expr
defined class N
defined class Var
defined class VarDecl
defined class Assign
defined class Deref
defined class A
defined function isValue
defined function isLValue

## Memories

In [11]:
// Mem is an abstract data type to represent memory, we use Map to implement it
// our memory is a map from memory addresses to expressions (always values)
// and the next addresss which is an int
sealed class Mem private (m: Map[A, Expr], nextAddr: Int) {

  // here, we use default implementations for lookups and toString
  def apply(a: A): Expr = m(a)
  override def toString: String = m.toString

  // this is for updating the memory (DoAssignVar)
  // we return a new memory that includes our updated "location"
  // in code, it will overwrite the mapping for a, but we want to think about it 
  // like it is updating the location which a is pointing to to a different value
  // infix because of fancy scala syntax
  def +(av: (A, Expr)): Mem = {
    val (a, _) = av
    require(m.contains(a))
    new Mem(m + av, nextAddr)
  }

  // allocates a new memeory cell in our memory
  // this is represented as a new mapping from address to value (entry in our map)
  // returns the address and the new memory
  def alloc(v: Expr): (A, Mem) = {
    val fresha = A(nextAddr)
    (fresha, new Mem(m + (fresha -> v), nextAddr + 1))
  }
}

object Mem {
  // "empty" memory
  val empty: Mem = new Mem(Map.empty, 1)
}

defined class Mem
defined object Mem

In [12]:
// examples
// ast 
val e_assign =
  VarDecl("i", N(1),
    Assign(Var("i"), N(2))
  )
// notice that the final memory is what we are really after here
// memory 
val (a, m) = Mem.empty.alloc(N(42))


e_assign: VarDecl = VarDecl(
  x = "i",
  e1 = N(n = 1.0),
  e2 = Assign(e1 = Var(x = "i"), e2 = N(n = 2.0))
)
a: A = A(a = 1)
m: Mem = Map(A(1) -> N(42.0))

## Substitute

In [13]:
// subsitute that we have seen before
def substitute(with_e: Expr, x: String, in_e: Expr) = {
  def subst(in_e: Expr): Expr = in_e match {
    case N(_) | A(_) => in_e
    case Var(y) => if (x == y) with_e else in_e
    case VarDecl(y, e1, e2) => if (x == y) VarDecl(y, subst(e1), e2) else VarDecl(y, subst(e1), subst(e2))
    case Assign(e1, e2) => Assign(subst(e1), subst(e2))
    case Deref(e1) => Deref(subst(e1))
  }
  subst(in_e)
}

defined function substitute

## Step First Try 

In [14]:
// taking (expression, memory) returning (expression, memory)... matching our judgment form
def step(e: Expr, m: Mem): (Expr, Mem) = e match {
  // DoDeref
  // we lookup the value at address a
  case Deref(a @ A(_)) => (m(a), m)
  
  // DoAssignVar
  // requiring that v is a value...
  // we step to the value, and 
  // a new memeory with a memory cell which has the adress point to the value
  // using our defined + 
  case Assign(Deref(a @ A(_)), v) if isValue(v) => (v, m + (a -> v))
  
  // DoVarDecl
  case VarDecl(x, v1, e2) if isValue(v1) => {
    // we allocate a new memory cell 
    // we already know it is not in the domain because of how we are managing alloc 
    val (a, m_) = m.alloc(v1)
    // subsitute the dref for x in e2, return that with new mem
    (substitute(Deref(a), x, e2), m_)
  }
  // SearchAssign
  case Assign(l1, e2) if isLValue(l1) => {
    // stepping right side to value
    // remember, that we could have memory updates from stepping e2 so we thread
    // annoying... we fix with encapsulating effects
    val (e2_, m_) = step(e2, m)
    (Assign(l1, e2_), m_)
  }
  
  // SearchVarDecl
  case VarDecl(x, e1, e2) => {
    // stepping e1 down to a value
    // same as above
    val (e1_, m_) = step(e1, m)
    (VarDecl(x, e1_, e2), m_)
  }
}


defined function step

In [15]:
// test 
val (e_assign_, m_)   = step(e_assign, Mem.empty)
val (e_assign__, m__) = step(e_assign_, m_)

e_assign_: Expr = Assign(e1 = Deref(e1 = A(a = 1)), e2 = N(n = 2.0))
m_: Mem = Map(A(1) -> N(1.0))
e_assign__: Expr = N(n = 2.0)
m__: Mem = Map(A(1) -> N(2.0))

## DoWith

In [16]:
// same as before
sealed class DoWith[S, A] private (doer: S => (S, A)) {
  def map[B](f: A => B): DoWith[S, B] = new DoWith[S, B]({ (s: S) => { val (s_, a) = doer(s); (s_, f(a)) } })
  def flatMap[B](f: A => DoWith[S, B]): DoWith[S, B] = new DoWith[S, B]({ (s: S) => { val (s_, a) = doer(s); f(a)(s_) } })
  def apply(s: S): (S, A) = doer(s)
}

object DoWith {
  def doget[S]: DoWith[S, S] = new DoWith[S, S]({ s => (s, s) })
  def doput[S](s: S): DoWith[S, Unit] = new DoWith[S, Unit]({ _ => (s, ()) })
  def doreturn[S, A](a: A): DoWith[S, A] = new DoWith[S, A]({ s => (s, a) })
  def domodify[S](f: S => S): DoWith[S, Unit] = new DoWith[S, Unit]({ s => (f(s), ()) })
}
import DoWith._

defined class DoWith
defined object DoWith
import DoWith._

## Update allocate 

In [17]:
// remeber we are defining something that creates a DoWith
// this means that if it is called, it is still waiting on 
// an initial state to start the chain of computation 

// doget gets current state, we then flatmap to provide a function that
// will return another DoWith... flatMap operates on the right part of the DoWith
// we are creating an instuction here
def memalloc(v: Expr): DoWith[Mem, A] = doget flatMap { m => 
  // now, we allocate memory for the value expression
  // we get back the addrees and new memory 
  val (a, m_) = m.alloc(v) 
  // now we want to put that memory in the state (doput)
  // then we want the right side to be the address
  doput(m_) map {_ => a}
}
// this whole thing is just creating a chain of functions that will execute when an initial value is passed in 
// it can be though of as a description of what to do

defined function memalloc

we can implement the judgment form as expr -> DoWith[Mem, A]

## New Step

In [18]:
// we now take an expr and return a DoWith[Mem, Expr], after supplying initial memory, our final result with be (Mem, Expr)
// we are encapsulating memory computations
def step(e: Expr): DoWith[Mem, Expr] = e match {
  // DoDeref
  case Deref(a @ A(_)) =>
    // lookup value at address 
    // we want to get the current memory... doGet to get the 
    // memory out, then change the right side the the value stored at the location
    // doGet needs a memory to get started... remember this returns a DoWith, which when given an initial state will start all this
    doget map { m => m(a) }

  // DoAssignVar
  case Assign(Deref(a @ A(_)), v) if isValue(v) =>
    // want to pass in a function that will modify memeory how we want
    // once that memory is modified, we want to map it so we have the expr on right (doModify returns a DoWith with unit on right)
    // we need the type param here becuase we're giving it a funciton that depends on it
    domodify[Mem](m => m + (a -> v)) map { _ => v }

  // DoVarDecl
  case VarDecl(x, v1, e2) if isValue(v1) =>
    // want to allocate the memory, 
    // that returns a DoWith that has the address on the right
    // want to update that to be the actual expression, which is the subsitute
    // don't need to change the memory
    memalloc(v1) map { a => substitute(Deref(a), x, e2) }

  // SearchAssign
  case Assign(l1, e2) if isLValue(l1) =>
    // we step to get a DoWith 
    // then we want to map to change the expression to our new expression
    step(e2) map { e2_ => Assign(l1, e2_) }

  // SearchVarDecl
  case VarDecl(x, e1, e2) =>
    // similar process
    step(e1) map { e1_ => VarDecl(x, e1_, e2) }
}
// notice that the search rules hide the state manipulations
// they are passed along in the DoWiths without needing to access them
// b/c map perserves the left side 

defined function step

In [19]:
// test 

// here, we run the step with the expression
// this creates the chain of doWiths
val myDoWith = step(e_assign)
// we then run the doWith with an inital memory to produce results
val res = myDoWith(Mem.empty)
// what the doWith returns is a tuple of memory, expression
// this can be seen by the return type of all of the encapsulated functions
val (m_, e_assign_) = res
// continue
val (m__, e_assign__) = step(e_assign_)(m_)

myDoWith: DoWith[Mem, Expr] = ammonite.$sess.cmd16$Helper$DoWith@29c27d46
res: (Mem, Expr) = (
  Map(A(1) -> N(1.0)),
  Assign(e1 = Deref(e1 = A(a = 1)), e2 = N(n = 2.0))
)
m_: Mem = Map(A(1) -> N(1.0))
e_assign_: Expr = Assign(e1 = Deref(e1 = A(a = 1)), e2 = N(n = 2.0))
m__: Mem = Map(A(1) -> N(2.0))
e_assign__: Expr = N(n = 2.0)

### More chaining computation

In [19]:
// we see we are still threading memory through each call of step 
// we should think that this can be avoided since we are using DoWiths

// still want to start with the init memory
// for the computation chain, we want to start by stepping e_assign
// now, we are left with a doWith, we want to take that expression out 
// and pass to step again. The memory will thread on its own
val (m__, e_assign__) = (step(e_assign) flatMap {e_ => step(e_)})(Mem.empty)
// or 
val (m__2, e_assign__2) = (step(e_assign) flatMap {step} )(Mem.empty)
// we use flatMap here because step returns another DoWith 
// furthermore we need this because we want to modify the memory in the function 
// we are giving to flatMap. This cannot be done with a map, it will just keep the same memory
// we want to thread the memory

m__: Mem = Map(A(1) -> N(2.0))
e_assign__: Expr = N(n = 2.0)
m__2: Mem = Map(A(1) -> N(2.0))
e_assign__2: Expr = N(n = 2.0)